In [1]:


import re
import time
from collections import defaultdict
 
import pandas as pd
import requests
from lxml import etree
from selenium import webdriver
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.chrome.service import Service
from webdriver_manager.chrome import ChromeDriverManager
from selenium import webdriver


from selenium.common.exceptions import NoSuchElementException, WebDriverException
from selenium.webdriver import ActionChains
from selenium.webdriver.common.by import By
from selenium.webdriver.common.keys import Keys
 
 

In [2]:
option = webdriver.ChromeOptions()
option.add_argument("--no-sandbox")
option.add_argument("--disable-dev-shm-usage")

# 使用 webdriver_manager 自动管理 ChromeDriver
driver = webdriver.Chrome(ChromeDriverManager().install(), options=option)

driver.get("https://www.dianping.com/")

C:\Users\89859\AppData\Local\Temp\ipykernel_15536\383109317.py:6: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(ChromeDriverManager().install(), options=option)


In [3]:
# 打开目标网页
driver.get("https://www.dianping.com/shop/H2g1coag1130huKW/review_all/p1")

# 定义等待时间
wait_time = 5
scroll_count = 200  # 翻页范围

# 定义要遍历的 div 范围
start_index = 1
end_index = 15

print("-----------------waiting page ready-----------------")

# 定义点击展开评价函数
def click_expand_buttons():
    try:
        more_buttons = driver.find_elements(By.CLASS_NAME, "more-words")
        for button in more_buttons:
            driver.execute_script("arguments[0].click();", button)
        print("All '展开评价' buttons clicked")
    except NoSuchElementException:
        print("No '展开评价' buttons found")

# 初始化评论列表和用户信息列表
all_contents = []
user_info_list = []

# 定义爬取用户信息的函数
def scrape_user_info():
    try:
        # 读取详细名称
        detailed_name = driver.find_element(By.XPATH, "/html/body/div[1]/div[2]/div[1]/div/div/div/div[2]/div[1]").text.replace("\n", " ")
        # 读取IP地址
        ip_address = driver.find_element(By.XPATH, "/html/body/div[1]/div[2]/div[1]/div/div/div/div[2]/div[2]/span[2]").text.replace("\n", " ")
        # 读取关注数量
        following_count = driver.find_element(By.XPATH, "/html/body/div[1]/div[2]/div[2]/div/div[1]/div/div/div[1]/ul/li[1]/a").text.replace("\n", " ")
        # 读取粉丝数量
        follower_count = driver.find_element(By.XPATH, "/html/body/div[1]/div[2]/div[2]/div/div[1]/div/div/div[1]/ul/li[2]/a").text.replace("\n", " ")
        # 读取点赞数量
        likes_count = driver.find_element(By.XPATH, "/html/body/div[1]/div[2]/div[2]/div/div[1]/div/div/div[1]/ul/li[3]").text.replace("\n", " ")
        # 读取注册时间
        registration_date = driver.find_element(By.XPATH, "/html/body/div[1]/div[2]/div[2]/div/div[1]/div/div/div[2]/p").text.replace("\n", " ")
        
        # 检查VIP图标
        try:
            vip_icon = driver.find_element(By.XPATH, "/html/body/div[1]/div[2]/div[1]/div/div/div/div[2]/div[1]/div[1]/a/i")
            vip_status = "vip" if vip_icon else "普通用户"
        except NoSuchElementException:
            vip_status = "普通用户"

        # 返回用户信息
        return [detailed_name, ip_address, following_count, follower_count, likes_count, registration_date, vip_status]
    except NoSuchElementException:
        print("用户信息元素未找到")
        return None  # 如果未找到元素，则返回None

# 开始循环抓取评论和用户信息
for _ in range(scroll_count):
    # 等待页面加载完成
    time.sleep(wait_time)

    # 点击展开评价
    click_expand_buttons()

    print("-----------------start collecting comments-----------------")

    # 遍历 div 范围
    contents = []
    for i in range(start_index, end_index + 1):
        try:
            d = driver.find_elements(By.XPATH, f'/html/body/div/div[2]/div[2]/div[3]/div[3]/div[3]/ul/li[{i}]')
            for element in d:
                content_members = []
                name_element = element.find_element(By.XPATH, f'/html/body/div/div[2]/div[2]/div[3]/div[3]/div[3]/ul/li[{i}]/div/div[1]/a')
                name = name_element.text
                
                # 如果name是"匿名用户"，则跳过用户信息爬取，但保存评论数据
                if name == "匿名用户":
                    print(f"用户 {name} 是匿名用户，跳过用户页面访问，但保存评论数据")
                    taste = element.find_element(By.XPATH, f'/html/body/div/div[2]/div[2]/div[3]/div[3]/div[3]/ul/li[{i}]/div/div[2]/span[2]/span[1]').text
                    environment = element.find_element(By.XPATH, f'/html/body/div/div[2]/div[2]/div[3]/div[3]/div[3]/ul/li[{i}]/div/div[2]/span[2]/span[2]').text
                    service = element.find_element(By.XPATH, f'/html/body/div/div[2]/div[2]/div[3]/div[3]/div[3]/ul/li[{i}]/div/div[2]/span[2]/span[3]').text
                    
                    # 获取评论内容
                    for j in range(3, 6):
                        try:
                            comments = element.find_element(By.XPATH, f'/html/body/div/div[2]/div[2]/div[3]/div[3]/div[3]/ul/li[{i}]/div/div[{j}]').text
                            if comments:
                                break
                        except NoSuchElementException:
                            continue

                    print(f"评论：{comments}")
                    
                    # 保存评论数据
                    content_members.append(name)
                    content_members.append(taste)
                    content_members.append(environment)
                    content_members.append(service)
                    content_members.append(comments)
                    contents.append(content_members)
                    continue  # 跳过用户信息爬取，继续下一个评论
                
                # 处理非匿名用户
                taste = element.find_element(By.XPATH, f'/html/body/div/div[2]/div[2]/div[3]/div[3]/div[3]/ul/li[{i}]/div/div[2]/span[2]/span[1]').text
                environment = element.find_element(By.XPATH, f'/html/body/div/div[2]/div[2]/div[3]/div[3]/div[3]/ul/li[{i}]/div/div[2]/span[2]/span[2]').text
                service = element.find_element(By.XPATH, f'/html/body/div/div[2]/div[2]/div[3]/div[3]/div[3]/ul/li[{i}]/div/div[2]/span[2]/span[3]').text
                
                print(name)
                print(taste)
                print(environment)
                print(service)
                
                # 获取评论内容
                for j in range(3, 6):
                    try:
                        comments = element.find_element(By.XPATH, f'/html/body/div/div[2]/div[2]/div[3]/div[3]/div[3]/ul/li[{i}]/div/div[{j}]').text
                        if comments:
                            break
                    except NoSuchElementException:
                        continue
                
                print(comments)
                content_members.append(name)
                content_members.append(taste)
                content_members.append(environment)
                content_members.append(service)
                content_members.append(comments)
                contents.append(content_members)

                # 尝试点击用户名称并跳转到用户主页，爬取用户信息
                try:
                    # 保存当前窗口句柄
                    original_window = driver.current_window_handle

                    # 点击用户名称，进入用户主页
                    driver.execute_script("arguments[0].click();", name_element)
                    time.sleep(3)  # 等待用户主页加载

                    # 切换到新的窗口
                    for window_handle in driver.window_handles:
                        if window_handle != original_window:
                            driver.switch_to.window(window_handle)
                            break

                    # 爬取用户信息
                    user_info = scrape_user_info()

                    if user_info:
                        print("用户信息:", user_info)
                        # 将用户信息保存到用户信息列表中
                        user_info_list.append(user_info)

                    # 关闭用户主页窗口
                    driver.close()

                    # 切换回原来的窗口
                    driver.switch_to.window(original_window)
                    time.sleep(2)  # 等待评论页重新加载
                except (NoSuchElementException, WebDriverException):
                    print(f"跳转用户页面失败或用户信息元素未找到，跳过此用户 {name}")
                    continue  # 跳过此评论，继续处理下一个评论

        except NoSuchElementException:
            print("没有找到评论")

    print("current page contents", contents)

    # 将当前页面的评论添加到所有评论列表中
    all_contents.extend(contents)
    print("all_contents", all_contents)

    # 构造下一页的 URL
    next_page_url = driver.find_element(By.CLASS_NAME, "NextPage").get_attribute("href")

    # 打开下一页的 URL
    if next_page_url:
        driver.get(next_page_url)
    else:
        print("没有找到下一页按钮")
        break

# 打印所有抓取到的评论
print("all contents", all_contents)

-----------------waiting page ready-----------------
All '展开评价' buttons clicked
-----------------start collecting comments-----------------
用户 匿名用户 是匿名用户，跳过用户页面访问，但保存评论数据
评论：在繁华的深圳，雨花西餐厅犹如一颗静谧的美食绿洲，让人惊喜不已。每一口菜品都凝聚了厨师的匠心独运，尤其是那道战斧牛排，肉质鲜嫩，香气四溢，简直是味蕾的盛宴。环境优雅，服务周到，每一处细节都透露着精致。在这里，我感受到了美食带来的幸福感，雨花西餐厅，值得我赋予五星好评！
收起评价
用户 匿名用户 是匿名用户，跳过用户页面访问，但保存评论数据
评论：进门没有服务员在门口，以为不开门，后面看到有人在用餐走到里面才有人过来，店内死气沉沉，服务员都不太热情，还没有走到餐桌服务员已经端起不知道什么时候接好的水跟我们一起过来，水杯略显的不干净，餐桌上的餐具🍽都有灰了跟朋友两人点了300多的套餐，都觉得只有炒饭的味道还不错，蘑菇不好吃，鱼柳好咸牛排🥩很一般，秉承着不浪费能吃下都吃的差不错了，我跟朋友都说不会再来了
收起评价
Nicole菲儿
口味：5.0
环境：5.0
服务：5.0
深圳颇具怀旧氛围感的西餐厅『雨花』 [薄荷]环境： 一楼拐弯泛白的明星合影有些年头，二楼墨绿色的主色调有点海派西餐厅的味道，类似的业态的名典咖啡、上岛咖啡早已无处遁形，雨花却在沧海桑田间还保留了最后一家，当时前卫的装修如今也变得有的vintage，深沉的墙面油画印，昏黄的灯光下，酒瓶、瓷器和贝母灯摆件拍照蛮有味道。 虽然是家老派西餐厅，现在也与时俱进结合了日料店『放题』的营销法，不同于之前的单点，现在花个百来块的单价就可以任点一款扒类主食，即可解锁所有30十副食自助放题。
收起评价
用户信息: ['Nicole菲儿 + 关注', '深圳', '关注 63', '粉丝 62', '获赞 314', '注册时间：2014-09-23', 'vip']
黄元帅
口味：2.5
环境：2.0
服务：2.5
今天过来消费优缺点我都讲下 先说不好的点。1 **上下了单，有诱导消费，说是均可用 但你买完才发现下面有行小字说明使用日期。单看以为能用下单 要拉到很下面才知道是周一-周

NoSuchElementException: Message: no such element: Unable to locate element: {"method":"css selector","selector":".NextPage"}
  (Session info: chrome=128.0.6613.114)
Stacktrace:
	GetHandleVerifier [0x011FD933+25811]
	(No symbol) [0x0118E314]
	(No symbol) [0x01082523]
	(No symbol) [0x010C7483]
	(No symbol) [0x010C765B]
	(No symbol) [0x01106BA2]
	(No symbol) [0x010EAD74]
	(No symbol) [0x011046F0]
	(No symbol) [0x010EAAC6]
	(No symbol) [0x010BBEFD]
	(No symbol) [0x010BC8FD]
	GetHandleVerifier [0x014CF143+2981091]
	GetHandleVerifier [0x01522FF9+3324825]
	GetHandleVerifier [0x0128B32F+605903]
	GetHandleVerifier [0x01292CBC+637020]
	(No symbol) [0x01196F4D]
	(No symbol) [0x01193DD8]
	(No symbol) [0x01193F75]
	(No symbol) [0x01186406]
	BaseThreadInitThunk [0x7661FA29+25]
	RtlGetAppContainerNamedObjectPath [0x77107A7E+286]
	RtlGetAppContainerNamedObjectPath [0x77107A4E+238]


In [4]:

# 将评论信息转换为DataFrame
df_comments = pd.DataFrame(all_contents, columns=['name','taste','environment','service', 'comment'])

# 将评论信息写入CSV文件
df_comments.to_csv('D:/Python/SCGC/大众点评dianping/dianping_new/raw_content_dianping_all2.csv', index=False)

# 将用户信息转换为DataFrame
df_users = pd.DataFrame(user_info_list, columns=['detailed_name', 'ip_address', 'following_count', 'follower_count', 'likes_count', 'registration_date','vip_status'])

# 将用户信息写入CSV文件
df_users.to_csv('D:/Python/SCGC/大众点评dianping/dianping_new/user_info_dianping_all2.csv', index=False)